In [1]:
import tensorflow as tf
from tensorflow.keras import layers, Model
from tensorflow.keras.optimizers import Adam
import pandas as pd
import numpy as np
from pathlib import Path
import os
import random
from plyfile import PlyData, PlyElement
import open3d as o3d
random.seed(42)
np.random.seed(42)
tf.random.set_seed(42)
from scipy.spatial import cKDTree

2025-03-07 12:43:40.937213: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-03-07 12:43:41.600897: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/fmartinez/cuda/cudnn/lib64:/usr/local/cuda/lib64:
2025-03-07 12:43:41.600955: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/fmartinez/cuda/cudnn/lib64:/usr/local/cuda/lib64:
2025-03-07 12:43:4

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
import numpy as np
import os
from pathlib import Path
from typing import List, Tuple
from tqdm import tqdm

NUM_POINTS = 1024 # 256, 512, 1024, 2048, 4096, 8192, 16384, 32768

category_mapping = {
    0: [43, 38, 58, 29, 41, 42, 44, 39, 55], # Construction
    1: [4, 45, 6, 40, 60, 61, 33, 32, 14], # Object
    2: [7, 22, 9, 26, 11, 21], # Road
    3: [48, 47, 1, 19, 46, 10, 25], # Sign
    4: [23, 3, 24, 31, 2], # Terrain  
    5: [51, 50, 5, 18], # Drivable Vegetation
    6: [28, 27, 62, 52, 16, 30, 59, 17], # Non Drivable Vegetation
    7: [13, 15, 12, 36, 57, 49, 20, 35, 37, 34, 63], # Vehicle
    8: [8, 56, 0, 53, 54], # Void
}

def filter_points_within_radius(points: np.ndarray, radius: float = 25.0) -> np.ndarray:
    distances = np.linalg.norm(points, axis=1) 
    mask = distances <= radius  
    return points[mask]  

def load_bin_file(bin_path: str, radius: float = 25.0) -> Tuple[np.ndarray, np.ndarray]:
    points = np.fromfile(bin_path, dtype=np.float32).reshape(-1, 4)[:, :3] 
    
    distances = np.linalg.norm(points, axis=1)
    mask = distances <= radius
    points_filtered = points[mask]  # Puntos después del filtrado
    indices_filtered = np.where(mask)[0]  # Índices originales de los puntos filtrados

    return points_filtered, indices_filtered

label_to_category = {label: cat for cat, labels in category_mapping.items() for label in labels}

def map_labels(labels: np.ndarray) -> np.ndarray:
    return np.array([label_to_category.get(label, 8) for label in labels], dtype=np.uint8)

def load_label_file(label_path: str, indices: np.ndarray) -> np.ndarray:
    labels = np.fromfile(label_path, dtype=np.uint32) & 0xFFFF 
    return map_labels(labels[indices]) 

def load_dataset(bin_files: List[str], label_files: List[str], num_points: int = NUM_POINTS) -> Tuple[np.ndarray, np.ndarray]:
    x_data, y_data = [], []
    
    for bin_f, label_f in tqdm(zip(bin_files, label_files), total=len(bin_files), desc="Cargando datos"):
        points, indices = load_bin_file(bin_f)
        
        if points.shape[0] < num_points:
            continue  

        labels = load_label_file(label_f, indices)

        x_data.append(points)
        y_data.append(labels)

    return np.array(x_data, dtype=np.float32), np.array(y_data, dtype=np.uint8)

def get_file_paths(data_dir: str) -> List[str]:
    return sorted([str(f) for f in Path(data_dir).glob("*.*")])

def load_all_data(x_train_dir: str, y_train_dir: str, x_val_dir: str, y_val_dir: str) -> Tuple[np.ndarray, np.ndarray, np.ndarray, np.ndarray]:
    x_train_files = get_file_paths(x_train_dir)
    y_train_files = get_file_paths(y_train_dir)
    x_val_files = get_file_paths(x_val_dir)
    y_val_files = get_file_paths(y_val_dir)
    
    assert len(x_train_files) == len(y_train_files), "Número de archivos x_train y y_train no coincide."
    assert len(x_val_files) == len(y_val_files), "Número de archivos x_val y y_val no coincide."
    
    print("Cargando datos de entrenamiento...")
    x_train, y_train = load_dataset(x_train_files, y_train_files)
    
    print("Cargando datos de validación...")
    x_val, y_val = load_dataset(x_val_files, y_val_files)
    
    return x_train, y_train, x_val, y_val

def get_train_sample(points, labels, n = 16384):
    """Obtiene una subnube de entrenamiento con N puntos desde la nube recortada."""
    center_idx = np.random.randint(len(points)) 
    tree = cKDTree(points) 
    _, neighbor_indices = tree.query(points[center_idx], k=n)  # Obtiene los n vecinos más cercanos

    return points[neighbor_indices], labels[neighbor_indices]

def load_bin_file_2(bin_path: str, num_points: int = NUM_POINTS, radius: float = 25.0) -> Tuple[np.ndarray, np.ndarray]:
    # Cargar la nube de puntos
    points = np.fromfile(bin_path, dtype=np.float32).reshape(-1, 4)[:, :3] 

    # Filtrar por distancia
    distances = np.linalg.norm(points, axis=1)
    mask = distances <= radius
    points = points[mask]

    num_available = points.shape[0]

    if num_available >= num_points:
        # Seleccionar un punto aleatorio
        center_idx = np.random.randint(0, num_available)

        # Calcular inicio y fin tratando de centrar la ventana
        half_span = num_points // 2
        start_idx = max(0, center_idx - half_span)
        end_idx = start_idx + num_points

        # Si nos pasamos del límite superior, compensar hacia atrás
        if end_idx > num_available:
            end_idx = num_available
            start_idx = max(0, end_idx - num_points)

        # Si nos pasamos del límite inferior, compensar hacia adelante
        if start_idx == 0:
            end_idx = min(num_available, num_points)

        indices = np.arange(start_idx, end_idx)
        return points[indices], np.where(mask)[0][indices]

    else:
        # Si hay menos de num_points disponibles, devolver todo lo que haya
        return points, np.where(mask)[0]


In [3]:
x_train_path = "/home/fmartinez/datasets/lidar/train"
y_train_path = "/home/fmartinez/datasets/labels/train"
x_val_path = "/home/fmartinez/datasets_val/lidar/val"
y_val_path = "/home/fmartinez/datasets_val/labels/val"

x_train_files = get_file_paths(x_train_path)
y_train_files = get_file_paths(y_train_path)
x_val_files = get_file_paths(x_val_path)
y_val_files = get_file_paths(y_val_path)

In [4]:
points, indices = load_bin_file(x_train_files[0])
labels = load_label_file(y_train_files[0], indices)

In [5]:
points_window, lables_window = get_train_sample(points, labels, 16384)

In [6]:
points_window.shape

(16384, 3)

In [7]:
import plotly.graph_objects as go
import numpy as np

def visualizar_nube_puntos(points, labels, title="Nube de Puntos 3D"):
    """
    Visualiza una nube de puntos en 3D con Plotly, coloreando los puntos según sus etiquetas.
    
    Parámetros:
        points (np.ndarray): Nube de puntos con forma (N, 3).
        labels (np.ndarray): Etiquetas de clase para cada punto.
        title (str, opcional): Título del gráfico.
    """
    fig = go.Figure()
    
    unique_labels = np.unique(labels)
    color_palette = ["gray", "orange", "blue", "red", "brown", "lightgreen", "darkgreen", "yellow", "black"]
    
    for i, class_id in enumerate(unique_labels):
        indices = np.where(labels == class_id)[0]
        if len(indices) > 0:
            fig.add_trace(go.Scatter3d(
                x=points[indices, 0],
                y=points[indices, 1],
                z=points[indices, 2],
                mode='markers',
                marker=dict(
                    size=2,
                    color=color_palette[i % len(color_palette)],
                    opacity=0.8
                ),
                name=f"Clase {class_id}"
            ))
    
    fig.update_layout(
        title=title,
        scene=dict(
            xaxis_title="X",
            yaxis_title="Y",
            zaxis_title="Z"
        )
    )
    
    fig.show()

In [8]:
points_window, lables_window = get_train_sample(points, labels, 16384)

In [28]:
visualizar_nube_puntos(points, labels)